# GR4H example

In [17]:
from pathlib import Path
import pandas as pd
from numpy import sqrt, mean
import datetime
from hydrogr import InputDataHandler, ModelGr4h
import plotly.graph_objects as go
from plotly.subplots import make_subplots

## Prepare the input data

Here we load a dataframe that contains daily rainfall and evapotranspiration data. The data is already daily sampled.
For demonstration purpose, we will not run the model on all the dataset period, but on a sub-period from 1989 to 1999.

Here the use of the InputDataHandler is not mandatory, as the model require a dataframe as input. But this class is an helper to ensure the data contains the mandatory time series, sampled at the correct frequency.
The class also provides a method to get a sub-period of the data.

In [3]:
data_path = Path.cwd().parent / 'data'
df = pd.read_pickle(data_path / 'L0123003.pkl')
df.columns = ['date', 'precipitation', 'temperature', 'evapotranspiration', 'flow', 'flow_mm']
df.index = df['date']

inputs = InputDataHandler(ModelGr4h, df)
inputs = inputs.get_sub_period(datetime.datetime(2004, 1, 1, 0, 0), datetime.datetime(2008, 1, 1, 0, 0))

## Setup the model

Here we define the model parameters and the initial states.
Model parameters are mandatory at model creation, and can be changed afterward using the set_parameters method.

In [4]:
# Set the model :
parameters = {
        "X1": 521.113,
        "X2": -2.918,
        "X3": 218.009,
        "X4": 4.124
    }
model = ModelGr4h(parameters)
model.set_parameters(parameters)  # Re-define the parameters for demonstration purpose.

# Initial state :
initial_states = {
    "production_store": 0.9,
    "routing_store": 0.9,
    "uh1": None,
    "uh2": None
}
model.set_states(initial_states)

## Run the model and display the results

In [5]:
outputs = model.run(inputs.data)
print(outputs.head())

                          flow
date                          
2004-01-01 00:00:00  22.322414
2004-01-01 01:00:00  13.071620
2004-01-01 02:00:00   9.000266
2004-01-01 03:00:00   6.754749
2004-01-01 04:00:00   5.347105


In [18]:
rmse = sqrt(mean((outputs['flow'].values - inputs.data['flow_mm'].values) ** 2.0))
print(rmse)

0.18625210940061873


In [16]:
fig = make_subplots(
    rows=2, cols=1,
    row_heights=[0.3, 0.7],
    shared_xaxes=True
)

fig.add_trace(
    go.Scatter(x=inputs.data.index, y=inputs.data['precipitation'], name="Precipitation"),
    row=1, col=1 
)
fig.update_yaxes(autorange="reversed", row=1, col=1)
fig.add_trace(
    go.Scatter(x=inputs.data.index, y=inputs.data['flow_mm'], name="Observed flow"),
    row=2, col=1 
)
fig.add_trace(
    go.Scatter(x=outputs.index, y=outputs['flow'], name="Calculated flow"),
    row=2, col=1 
)
fig.update_yaxes(range=[0, 5], row=2, col=1)

fig.update_layout(template='plotly_dark', title_text='GR4H')
fig.show()